In [10]:
from Bio import SeqIO
from Bio.SeqUtils import MeltingTemp as mt
#Tm_GC(seq)
import numpy as np
vic = [seq.seq for seq in SeqIO.parse("victoria-pb2.fasta", "fasta")][0]

def get_seqs(variants_file):
    """
    variant_file: fasta file of PB2 sequences
    
    Returns: list of SeqRecords for all PB2 sequences in fasta file
    """
    all_seq = []
    for seq in SeqIO.parse(variants_file, "fasta"):
        #trim sequences to ORF
        if str(seq.seq)[0:3] != "ATG":
            for index, base in enumerate(seq.seq):
                if seq.seq[index:index+3] == "ATG":
                    start = index
            seq.seq = seq.seq[start:start+2280]
        all_seq.append(seq)   
    return all_seq
def generate_tiles(get_seqs, tile_length, overlap, vic):
    """
    tile_length (int): the length of variable DNA per fragment
    overlap (int): length of overlap between tile fragments
    vic (str): PB2 sequence to use for overlap
    
    Returns: dictionary where keys are the id of the original PB2 sequence 
                and values are tuples of lists of the tiles generated from those sequences, 
                where the first list is the forward and the second is the reverse
    """
    tiles = {}
    first_tiles = []
    for seq in get_seqs:
        seq_tiles = []
        rev_tiles = []
        for i in range(0, len(seq.seq)-1, tile_length+overlap):
            if i == 0:
                new_tile = seq.seq[i:i+tile_length] + vic[i+tile_length:i+tile_length+overlap]
            elif i == len(seq.seq)-2:
                new_tile = vic[i-overlap:i] + seq.seq[i:i+tile_length]
            else:
                new_tile = vic[i-overlap:i] + seq.seq[i:i+tile_length] + vic[i+tile_length:i+tile_length+overlap]
            seq_tiles.append(str(new_tile))
            rev_tiles.append(str(new_tile.reverse_complement()))
        tiles[seq.id] = (seq_tiles, rev_tiles)
    return tiles
tiles = generate_tiles(get_seqs("AllUniqueDNA.fasta"), 180, 30, vic)
print(tiles)
#find the number of unique 5' end fragments
first_tiles = []
for seqs in tiles.values():
    first_tiles.append(str(seqs[0][0]))
unique = np.unique(first_tiles)
len(unique)

{'gb:KT838857|Organism:Influenza': (['ATGGAAAGAATAAAAGAACTACGGAATCTAATGTCGCAGTCTCGCACTCGCGAGATACTGACAAAAACCACAGTGGACCATATGGCCATAATTAAGAAGTACACATCGGGGAGACAGGAAAAGAACCCGTCACTTAGGATGAAATGGATGATGGCAATGAAATATCCAATCACTGCTGACAAAAGGGTAACAGAAATGGTTCCGGAGAGA', 'AAAAGGGTAACAGAAATGGTTCCGGAGAGAAATGAACAAGGACAAACTCTATGGAGTAAAATGAGTGATGCTGGATCAGATAGAGTGATGGTATCACCTTTGGCTGTAACATGGTGGAATAGGAATGGACCCGTGACAAATACGGTCCATTACCCAAAAGTGTACAAAACTTATTTCGACAAAGTCGAAAGGTTAAAACATGGAACCTTTGGCCCTGTCCATTTCAGAAATCAAGTCAAG', 'GGCCCTGTCCATTTCAGAAATCAAGTCAAGATACGCAGAAGAGTAGACATAAACCCTGGTCATGCAGACCTCAGTGCCAAAGAGGCACAAGATGTAATTATGGAAGTTGTTTTTCCCAATGAAGTGGGAGCCAGAATACTAACATCAGAATCACAGCTAACAATAACTAAAGAGAAAAAAGAAGAACTCCGAGATTGCAAAATTTCTCCCTTGATGGTCGCATACATGTTAGAGAGAGAA', 'TTGATGGTCGCATACATGTTAGAGAGAGAACTTGTGCGGAAAACAAGATTTCTCCCAGTTGCTGGCGGAACAAGCAGTATATACATTGAAGTTTTACATTTGACTCAAGGAACGTGTTGGGAACAAATGTACACTCCAGGTGGAGGAGTGAGGAATGACGATGTTGACCAAAGCCTAATTATTGCGGCCAGGAACATAGTAAGAAGAGCCGCAGTATCAGCAGATCCACTAGCATCTTTA', 'GCAGTATCAGCAGATC

230

Tests that I need to code:
- check that every 5' end fragment begins with ATG and is the same length
- 
